In [1]:
import matplotlib.pyplot as plt
%matplotlib inline
import os
import json
import pickle
import torch
import numpy as np
import re
from tqdm.notebook import tqdm
from sklearn.utils import shuffle
from transformers import AutoTokenizer
import warnings
warnings.filterwarnings("ignore")

In [2]:
model_type = 'SZTAKI-HLT/hubert-base-cc' # bert-base-multilingual-cased, SZTAKI-HLT/hubert-base-cc


data_path = f"D:/Data/neural-punctuator/"
os.makedirs(data_path + model_type, exist_ok=True)
file_path = data_path + "szeged.txt"

with open(file_path, 'r', encoding='utf-8') as f:
    text = f.readlines()
    
len(text), text[1]

(82100,
 ' A szállásunk egy Balaton melletti kis üdülőfaluban, Zamárdiban volt, a Postának az üdülőházában.\n')

In [3]:
from collections import OrderedDict

text = list(OrderedDict.fromkeys(text))
len(text)

80875

In [4]:
from sklearn.utils import shuffle

text = shuffle(text, random_state=0)

text[1]

' Ez jutott az eszébe önkéntelenül.\n'

In [5]:
tokenizer = AutoTokenizer.from_pretrained(model_type)

In [6]:
def clean_text(text):
    text = text.replace('!', '.')
    text = text.replace(':', ',')
    text = text.replace('--', ',')
    text = text.replace('_', ' ')
    text = text.replace('\\', ' per ')

    
    reg = "(?<=[a-zA-Z])-(?=[a-zA-Z]{2,})"
    r = re.compile(reg, re.DOTALL)
    text = r.sub(' ', text)
    
    text = text.replace('-', ',')
    text = text.replace(';', '.')
    text = text.replace(' ,', ',')
    text = text.replace('(', ', ')
    text = text.replace(')', ', ')
    
    text = text.replace('...', '')
    text = text.replace('.\"', ',')
    text = text.replace('"', ',')
    
    text = re.sub(r'\s-\s', ' , ', text)

    text = re.sub(r'--\s?--', '', text)   
    
    text = re.sub(r',\s?,', ', ', text)
    text = re.sub(r'\.[\s+.]+', '. ', text)
    
    text = re.sub(r',\s?,', ',', text)
    
    remove_space_before = [',', '?', '.', '!', '\n']
    for c in remove_space_before:
        text = text.replace(' ' + c, c)
    
    text = re.sub(r',\s+[\.,\s]+', ', ', text)
    text = re.sub(r'\.\s+[\.,\s]+', '. ', text)
    text = re.sub(r'\.[\.,]+', '.', text)
    text = re.sub(r'\,[\.,]+', ',', text)
    text = text.lstrip('.,?')
    
    text = re.sub(r'\s+', ' ', text)
    
    return text.strip().lower()

In [7]:
text = [clean_text(t) for t in text]
text = [t for t in text if len(t) > 0]
len(text), text[1]

(80873, 'ez jutott az eszébe önkéntelenül.')

In [8]:
# ' '.join(text[train_n:train_n+valid_n])

In [9]:
text[29545]

'nem lennék bunkó, begyöpösödött agyú, naiv ember.'

In [10]:
for i, t in enumerate(text):
    if 'hengerekre' in t:
        print(i, t)

9821 mind az 1884. évi xvi. törvénycikk, mind az 1921. évi liv. törvénycikk a szerzői jogról ismerte és tartalmazta már a nyilvános előadása jogát színművek, zeneművek és zenés színművek vonatkozásában, az 1975. évi 4. tvr. szabályozásának megfelelően, teljes körűen, azaz a szerzőnek kizárólagos jogot biztosítva a műve bármilyen módon vagy eljárással való nyilvános előadásának engedélyezésére, ezen túlmenően kitért az ún. mechanikai előadás, jogát is, azaz a közzétett művek vonatkozásában a, művek átvitelének jogát, a szerző beleegyezése nélkül is, mechanikai előadás céljára szolgáló készülékekre, állandó vagy cserélhető alkatrészeikre, lemezekre, hengerekre stb.


In [11]:
tokenizer.encode(".?,")

[2, 4575, 8308, 3576, 3]

In [12]:
target_token2id = {t: tokenizer.encode(t)[-2] for t in ".?,"}
target_token2id

{'.': 4575, '?': 8308, ',': 3576}

In [13]:
target_ids = list(target_token2id.values())
target_ids

[4575, 8308, 3576]

In [14]:
id2target = {
    0: 0,
    -1: -1,
}
for i, ti in enumerate(target_ids):
    id2target[ti] = i+1
target2id = {value: key for key, value in id2target.items()}

def create_target(text):
    encoded_words, targets = [], []
    
    words = text.split(' ')

    for word in tqdm(words):
        target = 0
        for target_token, target_id in target_token2id.items():
            if word.endswith(target_token):
                word = word.rstrip(target_token)
                target = id2target[target_id]

        encoded_word = tokenizer.encode(word, add_special_tokens=False)
        
        for w in encoded_word:
            encoded_words.append(w)
        for _ in range(len(encoded_word)-1):
            targets.append(-1)
        targets.append(target)
#         print([tokenizer._convert_id_to_token(ew) for ew in encoded_word], target)
        assert(len(encoded_word)>0)

    return encoded_words, targets

In [15]:
train_n = 70_000
valid_n = 8_000

train_text = ' '.join(text[:train_n])
valid_text = ' '.join(text[train_n:train_n+valid_n])
test_text = ' '.join(text[train_n+valid_n:])

len(train_text.split(' ')), len(valid_text.split(' ')), len(test_text.split(' '))

(1088454, 124834, 44425)

In [16]:
len(text) - train_n - valid_n

2873

In [17]:
train_text.split(' ')[154349-5:154349+5]

['cserélhető',
 'alkatrészeikre,',
 'lemezekre,',
 'hengerekre',
 'stb.',
 'a',
 'kereskedés',
 'első',
 'félórája',
 'után']

In [18]:
train_tokens, train_targets = create_target(train_text)
valid_tokens, valid_targets = create_target(valid_text)
test_tokens, test_targets = create_target(test_text)

In [19]:
# For backward campatibility
train_tokens, train_targets = [train_tokens], [train_targets]
valid_tokens, valid_targets = [valid_tokens], [valid_targets]
test_tokens, test_targets = [test_tokens], [test_targets]

In [20]:
os.makedirs(data_path + model_type, exist_ok=True)
with open(data_path + f'{model_type}/train_data.pkl', 'wb') as f:
    pickle.dump((train_tokens, train_targets), f)
with open(data_path + f'{model_type}/valid_data.pkl', 'wb') as f:
    pickle.dump((valid_tokens, valid_targets), f)
with open(data_path + f'{model_type}/test_data.pkl', 'wb') as f:
    pickle.dump((test_tokens, test_targets), f)

In [21]:
from collections import Counter

for ds in (train_targets, valid_targets, test_targets):
    c = Counter((t for targets in ds for t in targets))
    print('\t'.join([str(c[i]) for i in (1,2,3,0,-1)]))

81168	1808	120027	885451	424349
9218	198	13781	101637	48294
3370	75	4885	36095	17440


In [22]:
e = []
i = 0

raw_words = valid_text.split(' ')

for te, ta in zip(valid_tokens[0], valid_targets[0]):
    if ta == -1:
        e.append(te)
    else:
        e.append(te)
        print(f"{tokenizer.decode(e):15}\t{tokenizer.decode(target2id[ta]):10}\t{raw_words[i]}")
        e = []
        i += 1

a              	[ P A D ] 	a
danubius       	[ P A D ] 	danubius
hotels         	[ P A D ] 	hotels
rt             	.         	rt.
eladott        	[ P A D ] 	eladott
374            	[ P A D ] 	374
ezer           	[ P A D ] 	ezer
523            	[ P A D ] 	523
darab          	[ P A D ] 	darab
saját          	[ P A D ] 	saját
részvényt      	[ P A D ] 	részvényt
4. 100         	[ P A D ] 	4.100
forintos       	[ P A D ] 	forintos
részvényenkénti	[ P A D ] 	részvényenkénti
árfolyamon     	[ P A D ] 	árfolyamon
május          	[ P A D ] 	május
3, án          	,         	3,án,
majd           	[ P A D ] 	majd
ugyanennyiért  	[ P A D ] 	ugyanennyiért
visszavásárolta	[ P A D ] 	visszavásárolta
azokat         	,         	azokat,
közölte        	[ P A D ] 	közölte
a              	[ P A D ] 	a
társaság       	[ P A D ] 	társaság
a              	[ P A D ] 	a
magyar         	[ P A D ] 	magyar
tőkepiacban    	[ P A D ] 	tőkepiacban
hétfőn         	.         	hétfőn.
2              	[ P A D ] 	2
csapa

euróról        	,         	euróról,
tette          	[ P A D ] 	tette
közzé          	[ P A D ] 	közzé
a              	[ P A D ] 	a
magyar         	[ P A D ] 	magyar
nemzeti        	[ P A D ] 	nemzeti
bank           	,         	bank,
mnb            	,         	mnb,
kedden         	.         	kedden.
az             	[ P A D ] 	az
európai        	[ P A D ] 	európai
tudat          	[ P A D ] 	tudat
számára        	[ P A D ] 	számára
hosszú         	[ P A D ] 	hosszú
ideig          	[ P A D ] 	ideig
ez             	[ P A D ] 	ez
volt           	[ P A D ] 	volt
az             	[ P A D ] 	az
ókorról        	[ P A D ] 	ókorról
szerzett       	[ P A D ] 	szerzett
legfontosabb   	[ P A D ] 	legfontosabb
információ     	.         	információ.
ennél          	[ P A D ] 	ennél
szebb          	[ P A D ] 	szebb
vidéket        	[ P A D ] 	vidéket
még            	[ P A D ] 	még
életemben      	[ P A D ] 	életemben
nem            	[ P A D ] 	nem
láttam         	[ P A D ] 	láttam
soha           	.       

a              	[ P A D ] 	a
saját          	[ P A D ] 	saját
nevében        	,         	nevében,
de             	[ P A D ] 	de
a              	[ P A D ] 	a
részvénytársaság	[ P A D ] 	részvénytársaság
javára         	[ P A D ] 	javára
jár            	[ P A D ] 	jár
el             	,         	el,
valamint       	[ P A D ] 	valamint
azokat         	[ P A D ] 	azokat
a              	[ P A D ] 	a
részvénytársaság	[ P A D ] 	részvénytársaság
által          	[ P A D ] 	által
forgalomba     	[ P A D ] 	forgalomba
hozott         	[ P A D ] 	hozott
részvényeket   	[ P A D ] 	részvényeket
is             	,         	is,
amelyeket      	[ P A D ] 	amelyeket
a              	[ P A D ] 	a
részvénytársaság	[ P A D ] 	részvénytársaság
követelése     	[ P A D ] 	követelése
biztosítékául  	[ P A D ] 	biztosítékául
kapott         	.         	kapott.
a              	[ P A D ] 	a
budapesti      	[ P A D ] 	budapesti
értéktőzsde    	[ P A D ] 	értéktőzsde
hivatalos      	[ P A D ] 	hivatalos
részvényindexe 

működését      	,         	működését,
áll            	[ P A D ] 	áll
a              	[ P A D ] 	a
magyar         	[ P A D ] 	magyar
nemzeti        	[ P A D ] 	nemzeti
bank           	[ P A D ] 	bank
közleményében  	,         	közleményében,
amelyet        	[ P A D ] 	amelyet
hétfőn         	[ P A D ] 	hétfőn
juttatott      	[ P A D ] 	juttatott
el             	[ P A D ] 	el
az             	[ P A D ] 	az
mti            	[ P A D ] 	mti
hez            	.         	hez.
a              	[ P A D ] 	a
bank           	[ P A D ] 	bank
austria        	[ P A D ] 	austria
májusban       	[ P A D ] 	májusban
képviseletet   	[ P A D ] 	képviseletet
nyit           	[ P A D ] 	nyit
belgrádban     	,         	belgrádban,
a              	[ P A D ] 	a
jugoszláv      	[ P A D ] 	jugoszláv
jegybank       	[ P A D ] 	jegybank
pénteken       	[ P A D ] 	pénteken
kiadta         	[ P A D ] 	kiadta
az             	[ P A D ] 	az
erre           	[ P A D ] 	erre
vonatkozó      	[ P A D ] 	vonatkozó
engedélyt      	

bevételre      	[ P A D ] 	bevételre
tehetnek       	[ P A D ] 	tehetnek
szert          	[ P A D ] 	szert
hirdetésekből  	,         	hirdetésekből,
és             	[ P A D ] 	és
további        	[ P A D ] 	további
1, 8           	[ P A D ] 	1,8
milliárd       	[ P A D ] 	milliárd
dollárra       	[ P A D ] 	dollárra
különböző      	[ P A D ] 	különböző
alkalmazásokból	,         	alkalmazásokból,
állítja        	[ P A D ] 	állítja
az             	[ P A D ] 	az
analysys       	[ P A D ] 	analysys
telekommunikációs	[ P A D ] 	telekommunikációs
piackutató     	[ P A D ] 	piackutató
cég            	.         	cég.
én             	[ P A D ] 	én
bűntársa       	[ P A D ] 	bűntársa
vagyok         	.         	vagyok.
őrület         	.         	őrület.
kiáltotta      	[ P A D ] 	kiáltotta
sári           	.         	sári.
múlt           	[ P A D ] 	múlt
heti           	[ P A D ] 	heti
bonni          	[ P A D ] 	bonni
villámlátogatásán	[ P A D ] 	villámlátogatásán
a              	[ P A D ] 	a
gymnic

...

becsapni       	.         	becsapni.
ezeket         	[ P A D ] 	ezeket
részben        	[ P A D ] 	részben
a              	[ P A D ] 	a
gt             	.         	gt.
új             	,         	új,
általános      	[ P A D ] 	általános
rendelkezései  	[ P A D ] 	rendelkezései
tartalmazzák   	,         	tartalmazzák,
részben        	[ P A D ] 	részben
az             	[ P A D ] 	az
egyes          	[ P A D ] 	egyes
társasági      	[ P A D ] 	társasági
formákra       	[ P A D ] 	formákra
vonatkozó      	[ P A D ] 	vonatkozó
rendelkezések  	.         	rendelkezések.
mi             	[ P A D ] 	mi
nem            	[ P A D ] 	nem
fürödtünk      	,         	fürödtünk,
de             	[ P A D ] 	de
volt           	[ P A D ] 	volt
ott            	[ P A D ] 	ott
egy            	[ P A D ] 	egy
3              	[ P A D ] 	3
személyes      	[ P A D ] 	személyes
hinta          	,         	hinta,
amire          	[ P A D ] 	amire
öten           	[ P A D ] 	öten
ültünk         	[ P A D ] 	ültünk
fel         

haza           	.         	haza.
mire           	[ P A D ] 	mire
készen         	[ P A D ] 	készen
lettem         	,         	lettem,
indulhattam    	[ P A D ] 	indulhattam
az             	[ P A D ] 	az
iskolába       	,         	iskolába,
mert           	[ P A D ] 	mert
korábban       	[ P A D ] 	korábban
oda            	[ P A D ] 	oda
kellett        	[ P A D ] 	kellett
érnünk         	,         	érnünk,
hogy           	[ P A D ] 	hogy
méltóképpen    	[ P A D ] 	méltóképpen
várjuk         	[ P A D ] 	várjuk
a              	[ P A D ] 	a
német          	[ P A D ] 	német
partnerségünket	.         	partnerségünket.
gyűlölöm       	.         	gyűlölöm.
az             	[ P A D ] 	az
informatikának 	[ P A D ] 	informatikának
az             	[ P A D ] 	az
üzleti         	[ P A D ] 	üzleti
célokat        	[ P A D ] 	célokat
kiszolgáló     	[ P A D ] 	kiszolgáló
eszköznek      	[ P A D ] 	eszköznek
kell           	[ P A D ] 	kell
lennie         	,         	lennie,
ugyanakkor     	[ P A D ] 	ugy

csak           	[ P A D ] 	csak
az             	[ P A D ] 	az
szjt           	.         	szjt.
új             	,         	új,
adhat          	[ P A D ] 	adhat
kivételt       	,         	kivételt,
ilyen          	[ P A D ] 	ilyen
kivétel        	[ P A D ] 	kivétel
pl             	.         	pl.
szabad         	[ P A D ] 	szabad
felhasználás   	,         	felhasználás,
egyes          	[ P A D ] 	egyes
jogosultságok  	[ P A D ] 	jogosultságok
díjigényre     	[ P A D ] 	díjigényre
való           	[ P A D ] 	való
korlátozása    	,         	korlátozása,
mint           	[ P A D ] 	mint
pl             	.         	pl.
az             	[ P A D ] 	az
ún             	.         	ún.
üreskazettajogdíj	,         	üreskazettajogdíj,
roppant        	[ P A D ] 	roppant
nadrágján      	[ P A D ] 	nadrágján
rántott        	[ P A D ] 	rántott
egyet          	,         	egyet,
és             	[ P A D ] 	és
elkacsázott    	[ P A D ] 	elkacsázott
csámpás        	,         	csámpás,
tempós         	[ P A D ] 	t

ideje          	[ P A D ] 	ideje
tehát          	[ P A D ] 	tehát
az             	[ P A D ] 	az
alábbi         	[ P A D ] 	alábbi
eseményekhez   	[ P A D ] 	eseményekhez
kötődik        	[ P A D ] 	kötődik
4              	[ P A D ] 	4
gyerekes       	[ P A D ] 	gyerekes
családanya     	[ P A D ] 	családanya
szeretnék      	[ P A D ] 	szeretnék
lenni          	.         	lenni.
de             	[ P A D ] 	de
ha             	[ P A D ] 	ha
kimondom       	[ P A D ] 	kimondom
ezt            	[ P A D ] 	ezt
a              	[ P A D ] 	a
szót           	,         	szót,
siena          	,         	siena,
az             	[ P A D ] 	az
az             	[ P A D ] 	az
érzésem        	,         	érzésem,
hogy           	[ P A D ] 	hogy
ott            	[ P A D ] 	ott
megláthatnék   	[ P A D ] 	megláthatnék
valamit        	,         	valamit,
amitől         	[ P A D ] 	amitől
minden         	[ P A D ] 	minden
rendbe         	[ P A D ] 	rendbe
jönne          	.         	jönne.
a              	[ P A D ] 	

például        	[ P A D ] 	például
a              	[ P A D ] 	a
telepítőkészletet	[ P A D ] 	telepítőkészletet
tartalmazó     	[ P A D ] 	tartalmazó
könyvtár       	[ P A D ] 	könyvtár
elérési        	[ P A D ] 	elérési
útját          	,         	útját,
azt            	[ P A D ] 	azt
megadhatjuk    	[ P A D ] 	megadhatjuk
a              	[ P A D ] 	a
per            	[ P A D ] 	per
per            	[ P A D ] 	per
számítógép     	[ P A D ] 	számítógép
per            	[ P A D ] 	per
könyvtár       	[ P A D ] 	könyvtár
per            	[ P A D ] 	per
alkönyvtár     	[ P A D ] 	alkönyvtár
per            	[ P A D ] 	per
per            	[ P A D ] 	per
alkönyvtár     	[ P A D ] 	alkönyvtár
per            	[ P A D ] 	per
állománynév    	[ P A D ] 	állománynév
alakban        	[ P A D ] 	alakban
is             	.         	is.
ebbe           	[ P A D ] 	ebbe
az             	[ P A D ] 	az
irodai         	[ P A D ] 	irodai
mindenesbe     	[ P A D ] 	mindenesbe
a              	[ P A D ] 	a
hp          

In [23]:
print(tokenizer.decode(valid_tokens[0]))

a danubius hotels rt eladott 374 ezer 523 darab saját részvényt 4. 100 forintos részvényenkénti árfolyamon május 3, án majd ugyanennyiért visszavásárolta azokat közölte a társaság a magyar tőkepiacban hétfőn 2 csapat volt az üzembiztonságot a magas rendelkezésre állást szolgálja az is hogy mind a központi telephelyen mind a hét regionális igazgatóságon redundáns hálózati eszközök működnek és redundáns összeköttetést biztosít az atm / frame relay gerinchálózat is a gyerekek sokkal szabadabbak nincs más dolguk csak az hogy tanuljanak sok érdekes játék volt még a játékok mind zsetonokkal működtek később aztán leértünk a buszunkhoz b szókincs magunk is egy buszra kapaszkodunk s csak futtából az ablakon át vizslatjuk a felbolydult durazzót például automatikusan letölti a hálózat felhasználói által gyakran használt weboldalakat és a saját példányát rendszeresen frissíti így azok a felhasználók akik a proxy kiszolgálón keresztül férnek hozzá a webhez az ilyen oldalakat megkaphatják közvetlenü

In [24]:
' '.join(text[train_n:train_n+valid_n])

"a danubius hotels rt. eladott 374 ezer 523 darab saját részvényt 4.100 forintos részvényenkénti árfolyamon május 3,án, majd ugyanennyiért visszavásárolta azokat, közölte a társaság a magyar tőkepiacban hétfőn. 2 csapat volt. az üzembiztonságot, a magas rendelkezésre állást szolgálja az is, hogy mind a központi telephelyen, mind a hét regionális igazgatóságon redundáns hálózati eszközök működnek, és redundáns összeköttetést biztosít az atm/frame relay gerinchálózat is. a gyerekek sokkal szabadabbak, nincs más dolguk csak az, hogy tanuljanak. sok érdekes játék volt, még a játékok mind zsetonokkal működtek. később aztán leértünk a buszunkhoz. b szókincs. magunk is egy buszra kapaszkodunk, s csak futtából, az ablakon át vizslatjuk a felbolydult durazzót. például automatikusan letölti a hálózat felhasználói által gyakran használt weboldalakat, és a saját példányát rendszeresen frissíti. így azok a felhasználók, akik a proxy kiszolgálón keresztül férnek hozzá a webhez, az ilyen oldalakat me